In [2]:
import os
import pandas as pd
import numpy as np
import math
from matplotlib.pyplot import *
import matplotlib.pyplot as plt
from matplotlib import animation
from matplotlib import cm
from parse import *
import seaborn as sns

In [3]:
CHUNKSIZE = 100000

TRAIN_PATH        = "../../data/train_StationPathInfo.csv"
TRAIN_PATH_EX     = "../../data/train_StationPathInfoEx.csv"
TEST_PATH         = "../../data/test_StationPathInfo.csv"
TEST_PATH_EX      = "../../data/test_StationPathInfoEx.csv"

TRAIN_DATE        = "../../data/train_date.csv"
TRAIN_NUMERIC     = "../../data/train_numeric.csv"
TRAIN_CATEGORICAL = "../../data/train_categorical.csv"
TEST_DATE         = "../../data/test_date.csv"
TEST_NUMERIC      = "../../data/test_numeric.csv"
TEST_CATEGORICAL  = "../../data/test_categorical.csv"

SEED = 0
CHUNKSIZE = 50000
NROWS = 1200000

ID_COLUMN = 'Id'
TARGET_COLUMN = 'Response'
STATION_NUM = 52
    
    

In [4]:
def is_bit_on(val, pos):
    mask = 1 << pos
    if val & mask:
        return 1
    else:
        return 0
    
def decode_categorical_data(df):
    for column_name, item in df.iteritems():
        if column_name != 'Id':
            vallist = item.unique()
            bitlist = []
            for val in vallist:
                if val != 0:
                    if val < 0:
                        val = val + 4294967296
                    bitpos = int(np.log2(float(val)))
                    bitlist.append(bitpos)

            for bit in bitlist:
                df[column_name + "_bit_" + str(bit)] = df[column_name].apply(lambda x:is_bit_on(x, bit))
            df.drop(column_name, axis=1, inplace=True)


In [5]:
def drop_duplicated_column(df):
    columns = df.columns
    col_num = len(columns)
    
    duplicated_cols = []
    for i in range(col_num-1):
        for j in range(i+1, col_num):
            print(i, j)
            col1 = columns[i]
            col2 = columns[j]

            if col1 != 'Id':
                if col1 not in duplicated_cols:
                    df_tmp = (df[col1] == df[col2])
                    if len(df_tmp) - df_tmp.sum() < 3:
                        duplicated_cols.append(col2)
    df.drop(duplicated_cols, axis=1, inplace=True)


In [6]:
station_id = 1
file_train_cat_dec = '../../data/train_categorical_dec_station_' + str(station_id) + '.csv' 
df = pd.read_csv(file_train_cat_dec, dtype='int32')
df_tmp = (df['L0_S1_F27'] != df['L0_S1_F31'])
df[df_tmp]


Id  L0_S1_F25  L0_S1_F27  L0_S1_F29  L0_S1_F31
1018785  2037603          0          0          1         24
1112195  2224683          0          0          1         48

In [7]:
station_id = 1
file_train_cat = '../../data/train_categorical_station_' + str(station_id) + '.csv' 
df = pd.read_csv(file_train_cat)
df[df['Id'] == 2037603]
df[df['Id'] == 116]

C:\Users\Tomonobu\Anaconda3\lib\site-packages\IPython\core\interactiveshell.py:2698: DtypeWarning: Columns (1,2,3,4) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


Id L0_S1_F25 L0_S1_F27 L0_S1_F29 L0_S1_F31
55  116       NaN       NaN       NaN       NaN

In [7]:

TRAIN_START_TIME     = "../../data/train_StartEndTime.csv"
df_start_train = pd.read_csv(TRAIN_START_TIME)

df_start_train[(df_start_train['Id'] == 2037603) | (df_start_train['Id'] == 2224683)]


Id  Response  StartTime  EndTime
1018785  2037603         0     572.21   573.76
1112195  2224683         0    1574.48  1577.50

S0 は F25 と F29 はほぼ重複しているが、重複しないIdが2つだけある。(Id 2037603, 2224683)
どちらも Response = 0 だし、
おそらく使えないが…

In [11]:
def bit_decode_categorical_data(station_id):
    file_train_cat_dec = '../../data/train_categorical_dec_station_' + str(station_id) + '.csv' 
    file_test_cat_dec  = '../../data/test_categorical_dec_station_' + str(station_id) + '.csv'
    file_test_cat_bitdec  = '../../data/all_categorical_bitdec_station_' + str(station_id) + '.csv'

    if os.path.exists(file_train_cat_dec) and os.path.exists(file_test_cat_dec):
        df_train = pd.read_csv(file_train_cat_dec, dtype='int32')
        df_test = pd.read_csv(file_test_cat_dec, dtype='int32')

        df_all = pd.concat([df_train, df_test])
        del df_train
        del df_test

        drop_duplicated_column(df_all)
        decode_categorical_data(df_all)

        df_all.to_csv(file_test_cat_bitdec, index=False)


In [12]:


for id in range (STATION_NUM):
    bit_decode_categorical_data(id)

0 1
0 2
0 3
0 4
1 2
1 3
1 4
2 3
2 4
3 4
0 1
0 2
0 3
0 4
0 5
0 6
0 7
0 8
0 9
0 10
0 11
0 12
0 13
0 14
0 15
0 16
0 17
0 18
1 2
1 3
1 4
1 5
1 6
1 7
1 8
1 9
1 10
1 11
1 12
1 13
1 14
1 15
1 16
1 17
1 18
2 3
2 4
2 5
2 6
2 7
2 8
2 9
2 10
2 11
2 12
2 13
2 14
2 15
2 16
2 17
2 18
3 4
3 5
3 6
3 7
3 8
3 9
3 10
3 11
3 12
3 13
3 14
3 15
3 16
3 17
3 18
4 5
4 6
4 7
4 8
4 9
4 10
4 11
4 12
4 13
4 14
4 15
4 16
4 17
4 18
5 6
5 7
5 8
5 9
5 10
5 11
5 12
5 13
5 14
5 15
5 16
5 17
5 18
6 7
6 8
6 9
6 10
6 11
6 12
6 13
6 14
6 15
6 16
6 17
6 18
7 8
7 9
7 10
7 11
7 12
7 13
7 14
7 15
7 16
7 17
7 18
8 9
8 10
8 11
8 12
8 13
8 14
8 15
8 16
8 17
8 18
9 10
9 11
9 12
9 13
9 14
9 15
9 16
9 17
9 18
10 11
10 12
10 13
10 14
10 15
10 16
10 17
10 18
11 12
11 13
11 14
11 15
11 16
11 17
11 18
12 13
12 14
12 15
12 16
12 17
12 18
13 14
13 15
13 16
13 17
13 18
14 15
14 16
14 17
14 18
15 16
15 17
15 18
16 17
16 18
17 18
0 1
0 2
0 3
0 4
0 5
0 6
0 7
0 8
0 9
0 10
0 11
0 12
0 13
0 14
0 15
0 16
0 17
0 18
1 2
1 3
1 4
1 5
1 6
1 7
1 8
1 9
1

12 16
12 17
12 18
12 19
12 20
12 21
12 22
12 23
12 24
12 25
12 26
12 27
12 28
12 29
12 30
12 31
12 32
12 33
12 34
12 35
12 36
12 37
12 38
12 39
13 14
13 15
13 16
13 17
13 18
13 19
13 20
13 21
13 22
13 23
13 24
13 25
13 26
13 27
13 28
13 29
13 30
13 31
13 32
13 33
13 34
13 35
13 36
13 37
13 38
13 39
14 15
14 16
14 17
14 18
14 19
14 20
14 21
14 22
14 23
14 24
14 25
14 26
14 27
14 28
14 29
14 30
14 31
14 32
14 33
14 34
14 35
14 36
14 37
14 38
14 39
15 16
15 17
15 18
15 19
15 20
15 21
15 22
15 23
15 24
15 25
15 26
15 27
15 28
15 29
15 30
15 31
15 32
15 33
15 34
15 35
15 36
15 37
15 38
15 39
16 17
16 18
16 19
16 20
16 21
16 22
16 23
16 24
16 25
16 26
16 27
16 28
16 29
16 30
16 31
16 32
16 33
16 34
16 35
16 36
16 37
16 38
16 39
17 18
17 19
17 20
17 21
17 22
17 23
17 24
17 25
17 26
17 27
17 28
17 29
17 30
17 31
17 32
17 33
17 34
17 35
17 36
17 37
17 38
17 39
18 19
18 20
18 21
18 22
18 23
18 24
18 25
18 26
18 27
18 28
18 29
18 30
18 31
18 32
18 33
18 34
18 35
18 36
18 37
18 38
18 39
19 20
19 2

27 41
27 42
27 43
27 44
27 45
28 29
28 30
28 31
28 32
28 33
28 34
28 35
28 36
28 37
28 38
28 39
28 40
28 41
28 42
28 43
28 44
28 45
29 30
29 31
29 32
29 33
29 34
29 35
29 36
29 37
29 38
29 39
29 40
29 41
29 42
29 43
29 44
29 45
30 31
30 32
30 33
30 34
30 35
30 36
30 37
30 38
30 39
30 40
30 41
30 42
30 43
30 44
30 45
31 32
31 33
31 34
31 35
31 36
31 37
31 38
31 39
31 40
31 41
31 42
31 43
31 44
31 45
32 33
32 34
32 35
32 36
32 37
32 38
32 39
32 40
32 41
32 42
32 43
32 44
32 45
33 34
33 35
33 36
33 37
33 38
33 39
33 40
33 41
33 42
33 43
33 44
33 45
34 35
34 36
34 37
34 38
34 39
34 40
34 41
34 42
34 43
34 44
34 45
35 36
35 37
35 38
35 39
35 40
35 41
35 42
35 43
35 44
35 45
36 37
36 38
36 39
36 40
36 41
36 42
36 43
36 44
36 45
37 38
37 39
37 40
37 41
37 42
37 43
37 44
37 45
38 39
38 40
38 41
38 42
38 43
38 44
38 45
39 40
39 41
39 42
39 43
39 44
39 45
40 41
40 42
40 43
40 44
40 45
41 42
41 43
41 44
41 45
42 43
42 44
42 45
43 44
43 45
44 45
0 1
0 2
0 3
0 4
0 5
0 6
0 7
0 8
0 9
0 10
0 11
0 12
0

0 258
0 259
0 260
0 261
0 262
0 263
0 264
0 265
0 266
0 267
0 268
0 269
0 270
0 271
0 272
0 273
0 274
0 275
0 276
0 277
0 278
0 279
0 280
0 281
0 282
0 283
0 284
0 285
0 286
0 287
0 288
0 289
0 290
0 291
0 292
0 293
0 294
0 295
0 296
0 297
0 298
0 299
0 300
0 301
0 302
0 303
0 304
0 305
0 306
0 307
0 308
0 309
0 310
0 311
0 312
0 313
0 314
0 315
0 316
0 317
0 318
0 319
0 320
0 321
0 322
0 323
0 324
0 325
0 326
0 327
0 328
0 329
0 330
0 331
0 332
0 333
0 334
0 335
0 336
0 337
0 338
0 339
0 340
0 341
0 342
0 343
0 344
0 345
0 346
0 347
0 348
0 349
0 350
0 351
0 352
0 353
0 354
0 355
0 356
0 357
0 358
0 359
0 360
0 361
0 362
0 363
0 364
0 365
0 366
0 367
0 368
0 369
0 370
0 371
0 372
0 373
0 374
0 375
0 376
0 377
0 378
0 379
0 380
0 381
0 382
0 383
0 384
0 385
0 386
0 387
0 388
0 389
0 390
0 391
0 392
0 393
0 394
0 395
0 396
0 397
0 398
0 399
0 400
0 401
0 402
0 403
0 404
0 405
0 406
0 407
0 408
0 409
0 410
0 411
0 412
0 413
0 414
0 415
0 416
0 417
0 418
0 419
0 420
0 421
0 422
0 423
0 42

2 344
2 345
2 346
2 347
2 348
2 349
2 350
2 351
2 352
2 353
2 354
2 355
2 356
2 357
2 358
2 359
2 360
2 361
2 362
2 363
2 364
2 365
2 366
2 367
2 368
2 369
2 370
2 371
2 372
2 373
2 374
2 375
2 376
2 377
2 378
2 379
2 380
2 381
2 382
2 383
2 384
2 385
2 386
2 387
2 388
2 389
2 390
2 391
2 392
2 393
2 394
2 395
2 396
2 397
2 398
2 399
2 400
2 401
2 402
2 403
2 404
2 405
2 406
2 407
2 408
2 409
2 410
2 411
2 412
2 413
2 414
2 415
2 416
2 417
2 418
2 419
2 420
2 421
2 422
2 423
2 424
2 425
2 426
2 427
2 428
2 429
2 430
2 431
2 432
2 433
2 434
2 435
2 436
2 437
2 438
2 439
2 440
2 441
2 442
2 443
2 444
2 445
2 446
2 447
2 448
2 449
2 450
2 451
2 452
2 453
2 454
2 455
2 456
2 457
2 458
2 459
2 460
2 461
2 462
2 463
2 464
2 465
2 466
2 467
2 468
2 469
2 470
2 471
2 472
2 473
2 474
2 475
2 476
2 477
2 478
2 479
2 480
2 481
2 482
2 483
2 484
2 485
2 486
2 487
2 488
2 489
2 490
2 491
2 492
2 493
2 494
2 495
2 496
2 497
2 498
2 499
2 500
2 501
2 502
2 503
2 504
2 505
2 506
2 507
2 508
2 509
2 51

...

117 203
117 204
118 119
118 120
118 121
118 122
118 123
118 124
118 125
118 126
118 127
118 128
118 129
118 130
118 131
118 132
118 133
118 134
118 135
118 136
118 137
118 138
118 139
118 140
118 141
118 142
118 143
118 144
118 145
118 146
118 147
118 148
118 149
118 150
118 151
118 152
118 153
118 154
118 155
118 156
118 157
118 158
118 159
118 160
118 161
118 162
118 163
118 164
118 165
118 166
118 167
118 168
118 169
118 170
118 171
118 172
118 173
118 174
118 175
118 176
118 177
118 178
118 179
118 180
118 181
118 182
118 183
118 184
118 185
118 186
118 187
118 188
118 189
118 190
118 191
118 192
118 193
118 194
118 195
118 196
118 197
118 198
118 199
118 200
118 201
118 202
118 203
118 204
119 120
119 121
119 122
119 123
119 124
119 125
119 126
119 127
119 128
119 129
119 130
119 131
119 132
119 133
119 134
119 135
119 136
119 137
119 138
119 139
119 140
119 141
119 142
119 143
119 144
119 145
119 146
119 147
119 148
119 149
119 150
119 151
119 152
119 153
119 154
119 155
119 156


134 140
134 141
134 142
134 143
134 144
134 145
134 146
134 147
134 148
134 149
134 150
134 151
134 152
134 153
134 154
134 155
134 156
134 157
134 158
134 159
134 160
134 161
134 162
134 163
134 164
134 165
134 166
134 167
134 168
134 169
134 170
134 171
134 172
134 173
134 174
134 175
134 176
134 177
134 178
134 179
134 180
134 181
134 182
134 183
134 184
134 185
134 186
134 187
134 188
134 189
134 190
134 191
134 192
134 193
134 194
134 195
134 196
134 197
134 198
134 199
134 200
134 201
134 202
134 203
134 204
135 136
135 137
135 138
135 139
135 140
135 141
135 142
135 143
135 144
135 145
135 146
135 147
135 148
135 149
135 150
135 151
135 152
135 153
135 154
135 155
135 156
135 157
135 158
135 159
135 160
135 161
135 162
135 163
135 164
135 165
135 166
135 167
135 168
135 169
135 170
135 171
135 172
135 173
135 174
135 175
135 176
135 177
135 178
135 179
135 180
135 181
135 182
135 183
135 184
135 185
135 186
135 187
135 188
135 189
135 190
135 191
135 192
135 193
135 194
135 195


154 180
154 181
154 182
154 183
154 184
154 185
154 186
154 187
154 188
154 189
154 190
154 191
154 192
154 193
154 194
154 195
154 196
154 197
154 198
154 199
154 200
154 201
154 202
154 203
154 204
155 156
155 157
155 158
155 159
155 160
155 161
155 162
155 163
155 164
155 165
155 166
155 167
155 168
155 169
155 170
155 171
155 172
155 173
155 174
155 175
155 176
155 177
155 178
155 179
155 180
155 181
155 182
155 183
155 184
155 185
155 186
155 187
155 188
155 189
155 190
155 191
155 192
155 193
155 194
155 195
155 196
155 197
155 198
155 199
155 200
155 201
155 202
155 203
155 204
156 157
156 158
156 159
156 160
156 161
156 162
156 163
156 164
156 165
156 166
156 167
156 168
156 169
156 170
156 171
156 172
156 173
156 174
156 175
156 176
156 177
156 178
156 179
156 180
156 181
156 182
156 183
156 184
156 185
156 186
156 187
156 188
156 189
156 190
156 191
156 192
156 193
156 194
156 195
156 196
156 197
156 198
156 199
156 200
156 201
156 202
156 203
156 204
157 158
157 159
157 160


2 4
2 5
2 6
2 7
2 8
3 4
3 5
3 6
3 7
3 8
4 5
4 6
4 7
4 8
5 6
5 7
5 8
6 7
6 8
7 8
0 1
0 2
0 3
1 2
1 3
2 3
0 1
0 2
0 3
0 4
0 5
0 6
0 7
0 8
0 9
0 10
0 11
0 12
0 13
0 14
0 15
0 16
0 17
0 18
1 2
1 3
1 4
1 5
1 6
1 7
1 8
1 9
1 10
1 11
1 12
1 13
1 14
1 15
1 16
1 17
1 18
2 3
2 4
2 5
2 6
2 7
2 8
2 9
2 10
2 11
2 12
2 13
2 14
2 15
2 16
2 17
2 18
3 4
3 5
3 6
3 7
3 8
3 9
3 10
3 11
3 12
3 13
3 14
3 15
3 16
3 17
3 18
4 5
4 6
4 7
4 8
4 9
4 10
4 11
4 12
4 13
4 14
4 15
4 16
4 17
4 18
5 6
5 7
5 8
5 9
5 10
5 11
5 12
5 13
5 14
5 15
5 16
5 17
5 18
6 7
6 8
6 9
6 10
6 11
6 12
6 13
6 14
6 15
6 16
6 17
6 18
7 8
7 9
7 10
7 11
7 12
7 13
7 14
7 15
7 16
7 17
7 18
8 9
8 10
8 11
8 12
8 13
8 14
8 15
8 16
8 17
8 18
9 10
9 11
9 12
9 13
9 14
9 15
9 16
9 17
9 18
10 11
10 12
10 13
10 14
10 15
10 16
10 17
10 18
11 12
11 13
11 14
11 15
11 16
11 17
11 18
12 13
12 14
12 15
12 16
12 17
12 18
13 14
13 15
13 16
13 17
13 18
14 15
14 16
14 17
14 18
15 16
15 17
15 18
16 17
16 18
17 18
0 1
0 2
0 3
0 4
0 5
0 6
0 7
0 8
1 2
1 3
1 4
1 5
1 

7 10
7 11
7 12
7 13
7 14
7 15
7 16
7 17
7 18
7 19
7 20
7 21
8 9
8 10
8 11
8 12
8 13
8 14
8 15
8 16
8 17
8 18
8 19
8 20
8 21
9 10
9 11
9 12
9 13
9 14
9 15
9 16
9 17
9 18
9 19
9 20
9 21
10 11
10 12
10 13
10 14
10 15
10 16
10 17
10 18
10 19
10 20
10 21
11 12
11 13
11 14
11 15
11 16
11 17
11 18
11 19
11 20
11 21
12 13
12 14
12 15
12 16
12 17
12 18
12 19
12 20
12 21
13 14
13 15
13 16
13 17
13 18
13 19
13 20
13 21
14 15
14 16
14 17
14 18
14 19
14 20
14 21
15 16
15 17
15 18
15 19
15 20
15 21
16 17
16 18
16 19
16 20
16 21
17 18
17 19
17 20
17 21
18 19
18 20
18 21
19 20
19 21
20 21


In [13]:
TRAIN_PATH        = "../../data/train_StationPathInfo.csv"

In [14]:

df_train_bin = pd.read_csv(TRAIN_PATH)
df_train_bin[df_train_bin['Id'] == 2037603]

Id  L0_S0_D1  L0_S1_D26  L0_S2_D34  L0_S3_D70  L0_S4_D106  \
1018785  2037603         1          0          1          0           1   

         L0_S5_D115  L0_S6_D120  L0_S7_D137  L0_S8_D145      ...       \
1018785           0           0           1           1      ...        

         L3_S42_D4029  L3_S43_D4062  L3_S44_D4101  L3_S45_D4125  L3_S46_D4135  \
1018785             0             0             0             0             0   

         L3_S47_D4140  L3_S48_D4194  L3_S49_D4208  L3_S50_D4242  L3_S51_D4255  
1018785             0             0             0             0             0  

[1 rows x 53 columns]